In [194]:
import calendar
import pandas as pd
import numpy as np
import requests
import pickle
import plotly.express as px
import plotly.graph_objects as go

import sys
sys.path.append("../")
import src.soporte as sp
import src.biblioteca as bb

pd.set_option('max_colwidth', None)
pd.set_option("display.max_columns", None)


In [4]:
df = pd.read_csv("../data/demanda.csv")

In [5]:
df["datetime"] = pd.to_datetime(df["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
df['datetime'] = df['datetime'].dt.tz_convert('Europe/Paris')

In [6]:

df_year = df[df["datetime"].dt.year == 2014]

In [426]:
fig1 = px.line(df_year, x = "datetime", y = "value", line_group = None)
mean_value = df_year['value'].mean()
fig1.add_shape(go.layout.Shape(
        type = "line",
        x0 = df_year['datetime'].iloc[0],
        y0 = mean_value,
        x1 = df_year['datetime'].iloc[-1],
        y1 = mean_value,
        line = dict(color = "black", width = 2, dash = "dot")))

fig1.show()

In [ ]:
def px_demanda(año):
    df_year = df[df["datetime"].dt.year == int(año)]
    fig1 = px.line(df_year, x = "datetime", y = "value", line_group = None)
    fig1.show()

In [416]:
df2 = pd.read_csv("../data/scrap/demanda_tiempo_real.csv")
df2.drop(["percentage_Demanda real", "percentage_Demanda programada", "percentage_Demanda prevista"], axis = 1, inplace = True)
df2["datetime"] = pd.to_datetime(df2["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
df2['datetime'] = df2['datetime'].dt.tz_convert('Europe/Paris')

In [417]:
df2

datetime  value_Demanda real  \
0      2014-01-01 00:00:00+01:00               24546   
1      2014-01-01 00:10:00+01:00               24309   
2      2014-01-01 00:20:00+01:00               24348   
3      2014-01-01 00:30:00+01:00               24321   
4      2014-01-01 00:40:00+01:00               24194   
...                          ...                 ...   
531163 2023-03-31 23:35:00+02:00               23983   
531164 2023-03-31 23:40:00+02:00               23926   
531165 2023-03-31 23:45:00+02:00               23550   
531166 2023-03-31 23:50:00+02:00               23605   
531167 2023-03-31 23:55:00+02:00               23406   

        value_Demanda programada  value_Demanda prevista  
0                          24099                   24482  
1                          24099                   24147  
2                          24099                   23882  
3                          24099                   23688  
4                          24099                   23563  
...                          ...                     ...  
531163                     23790                   24007  
531164                     23790                   23946  
531165                     23491                   23896  
531166                     23491                   23851  
531167                     23491                   23802  

[531168 rows x 4 columns]

In [425]:
año = 2014
semana_del_año = 25
df_year2 = df2[df2["datetime"].dt.year == int(año)]
df_week2 = df_year2[df_year2["datetime"].dt.isocalendar().week == int(semana_del_año)]
mean_value = df_week2["value_Demanda real"].mean()
fig = px.line(df_week2, x='datetime', y=["value_Demanda real", "value_Demanda programada", "value_Demanda prevista"], color_discrete_sequence=['blue', 'red', "green"])
fig.add_shape(go.layout.Shape(
        type = "line",
        x0 = df_week2['datetime'].iloc[0],
        y0 = mean_value,
        x1 = df_week2['datetime'].iloc[-1],
        y1 = mean_value,
        line = dict(color = "black", width = 2, dash = "dot")))
fig.show()


In [432]:
df2 = pd.read_csv("../data/scrap/demanda_tiempo_real.csv")
df2.drop(["percentage_Demanda real", "percentage_Demanda programada", "percentage_Demanda prevista"], axis = 1, inplace = True)
df2["datetime"] = pd.to_datetime(df2["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
df2["drop"] = df2["datetime"].where(df2["datetime"].dt.minute % 10 == 0, other= "drop")

In [511]:
df3 = pd.read_csv("../data/scrap/demanda_tiempo_real.csv")
df3.drop(["percentage_Demanda real", "percentage_Demanda programada", "percentage_Demanda prevista"], axis = 1, inplace = True)
df3["datetime"] = pd.to_datetime(df3["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
df3["drop"] = df3["datetime"].where(df3["datetime"].dt.minute % 10 == 0, other= "drop")
df3 = df3[df3["drop"] != "drop"]
df3.drop(["drop"], inplace = True, axis = 1)
estaciones = {"Primavera": ["03-20", "06-20"],
              "Verano": ["06-21", "09-22"],
              "Otoño": ["09-22", "12-21"],
              "Invierno": ["12-22", "03-19"]}
df_estaciones = pd.DataFrame()
for k,v in estaciones.items():
    estacion_todo = pd.DataFrame()
    for year in range(2013,2024):
        inicio = pd.to_datetime(f'{year}-{v[0]} 00:00:00+01:00')
        if k == "Invierno":
            fin = pd.to_datetime(f'{year+1}-{v[1]} 23:59:59+02:00')
        else: 
            fin = pd.to_datetime(f'{year}-{v[1]} 23:59:59+02:00')
        df_estacion_año = df3[(df3["datetime"] >= inicio) & (df3["datetime"] <= fin)]
        estacion_todo = pd.concat([estacion_todo, df_estacion_año], axis = 0)
    estacion_todo["dia"] = estacion_todo["datetime"].dt.day_of_week
    estacion_todo['hour'] = estacion_todo['datetime'].dt.hour
    estacion_todo['minute'] = estacion_todo['datetime'].dt.minute
    estacion_semana = estacion_todo.groupby(by = ['dia', 'hour', 'minute'])["value_Demanda real"].mean().reset_index()
    estacion = pd.DataFrame(estacion_semana["value_Demanda real"])
    estacion.columns = [f"Demanda {k}"]
    df_estaciones = pd.concat([df_estaciones, estacion], axis = 1, ignore_index= True)

df_estaciones.columns = ["Primavera", "Verano", "Otoño", "Invierno"]
df_estaciones["Día"]= [n+1 for n in range(df_estaciones.shape[0])]

In [512]:
mean_value = df_estaciones['Verano'].mean()
fig = px.line(
        df_estaciones,
        x='Día',
        y = ["Primavera", "Verano", "Otoño", "Invierno"],
        color_discrete_map = {"Primavera":"green", 'Verano':'red', "Otoño":"orange", "Invierno":"royalblue"})
fig.update_layout(
    xaxis=dict(
        tickvals=[87+ (144*n) for n in range(0,7)],
        ticktext=["Lunes", "Martes", "Miércoles", "Jueves", "Viernes", "Sábado", "Domingo"]))
fig.add_shape(go.layout.Shape(
        type = "line",
        x0 = df_estaciones['Día'].iloc[0],
        y0 = mean_value,
        x1 = df_estaciones['Día'].iloc[-1],
        y1 = mean_value,
        line = dict(color = "black", width = 2, dash = "dot")))
fig.show()

In [433]:
df2 = df2[df2["drop"] != "drop"]
df2.drop(["drop"], inplace = True, axis = 1)

In [434]:
df_primavera = pd.DataFrame()
for year in range(2013,2024):
    inicio = pd.to_datetime(f'{year}-03-20 00:00:00+01:00')
    fin = pd.to_datetime(f'{year}-06-20 23:59:59+02:00')
    df_primavera_año = df2[(df2['datetime'] >= inicio) & (df2['datetime'] <= fin)]
    df_primavera = pd.concat([df_primavera,df_primavera_año], axis = 0)
df_primavera["dia"] = df_primavera["datetime"].dt.day_of_week
df_primavera['hour'] = df_primavera['datetime'].dt.hour
df_primavera['minute'] = df_primavera['datetime'].dt.minute


In [446]:
primavera_semana = df_primavera.groupby(by = ['dia', 'hour', 'minute'])["value_Demanda real"].mean().reset_index()

In [464]:
primavera = pd.DataFrame(primavera_semana["value_Demanda real"])

In [467]:
primavera["dato"] = [n+1 for n in range(0, primavera.shape[0])]

In [436]:
fig = px.line(primavera_semana, x='index', y = "value_Demanda real", color_discrete_sequence=['blue'])
fig.show()

In [469]:
df_verano = pd.DataFrame()
for year in range(2013,2024):
    inicio = pd.to_datetime(f'{year}-06-21 00:00:00+01:00')
    fin = pd.to_datetime(f'{year}-09-22 23:59:59+02:00')
    df_verano_año = df2[(df2['datetime'] >= inicio) & (df2['datetime'] <= fin)]
    df_verano = pd.concat([df_verano, df_verano_año], axis = 0)
df_verano["dia"] = df_verano["datetime"].dt.day_of_week
df_verano['hour'] = df_verano['datetime'].dt.hour
df_verano['minute'] = df_verano['datetime'].dt.minute

In [470]:
verano_semana = df_verano.groupby(by = ['dia', 'hour', 'minute'])["value_Demanda real"].mean().reset_index().reset_index()

In [479]:
verano_semana

index  dia  hour  minute  value_Demanda real
0         0    0     0       0        23250.363636
1         1    0     0      10        23090.272727
2         2    0     0      20        22973.917355
3         3    0     0      30        22792.958678
4         4    0     0      40        22725.487603
...     ...  ...   ...     ...                 ...
1003   1003    6    23      10        24311.727273
1004   1004    6    23      20        24091.628099
1005   1005    6    23      30        23861.140496
1006   1006    6    23      40        23654.834711
1007   1007    6    23      50        23493.190083

[1008 rows x 5 columns]

In [471]:
fig = px.line(verano_semana, x='index', y = "value_Demanda real", color_discrete_sequence=['blue'])
fig.show()

In [474]:
df_otoño = pd.DataFrame()
for year in range(2013,2024):
    inicio = pd.to_datetime(f'{year}-09-22 00:00:00+01:00')
    fin = pd.to_datetime(f'{year}-12-21 23:59:59+02:00')
    df_otoño_año = df2[(df2['datetime'] >= inicio) & (df2['datetime'] <= fin)]
    df_otoño = pd.concat([df_otoño, df_otoño_año], axis = 0)
df_otoño["dia"] = df_otoño["datetime"].dt.day_of_week
df_otoño['hour'] = df_otoño['datetime'].dt.hour
df_otoño['minute'] = df_otoño['datetime'].dt.minute
otoño_semana = df_otoño.groupby(by = ['dia', 'hour', 'minute'])["value_Demanda real"].mean().reset_index().reset_index()

In [475]:
fig = px.line(otoño_semana, x='index', y = "value_Demanda real", color_discrete_sequence=['blue'])
fig.show()

In [480]:
df_invierno = pd.DataFrame()
for year in range(2013,2024):
    inicio = pd.to_datetime(f'{year}-12-22 00:00:00+01:00')
    fin = pd.to_datetime(f'{year + 1}-03-19 23:59:59+02:00')
    df_invierno_año = df2[(df2['datetime'] >= inicio) & (df2['datetime'] <= fin)]
    df_invierno = pd.concat([df_invierno, df_invierno_año], axis = 0)
df_invierno["dia"] = df_invierno["datetime"].dt.day_of_week
df_invierno['hour'] = df_invierno['datetime'].dt.hour
df_invierno['minute'] = df_invierno['datetime'].dt.minute
invierno_semana = df_invierno.groupby(by = ['dia', 'hour', 'minute'])["value_Demanda real"].mean().reset_index().reset_index()

In [481]:
fig = px.line(invierno_semana, x='index', y = "value_Demanda real", color_discrete_sequence=['blue'])
fig.show()

In [444]:

def px_demanda_real(año, semana_del_año):
    df_year2 = df2[df2["datetime"].dt.year == int(año)]
    df_week2 = df_year2[df_year2["datetime"].dt.isocalendar().week == int(semana_del_año)]
    fig = px.line(df_week2, x='datetime', y=["value_Demanda real", "value_Demanda programada", "value_Demanda prevista"], color_discrete_sequence=['blue', 'red', "green"])
    fig.show()

In [515]:
df3 = pd.read_csv("../data/scrap/precios_mercados.csv")
df3["datetime"] = pd.to_datetime(df3["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
df3['datetime'] = df3['datetime'].dt.tz_convert('Europe/Paris')

In [516]:
df3

value                  datetime
0       20.02 2014-01-01 00:00:00+01:00
1       10.34 2014-01-01 01:00:00+01:00
2        5.35 2014-01-01 02:00:00+01:00
3        5.00 2014-01-01 03:00:00+01:00
4        0.50 2014-01-01 04:00:00+01:00
...       ...                       ...
81033  115.17 2023-03-31 19:00:00+02:00
81034  130.72 2023-03-31 20:00:00+02:00
81035  133.53 2023-03-31 21:00:00+02:00
81036   85.18 2023-03-31 22:00:00+02:00
81037   84.34 2023-03-31 23:00:00+02:00

[81038 rows x 2 columns]

In [517]:
df4 = df3.copy()
df4['mes_y_año'] = df4['datetime'].dt.strftime('%m-%Y')
df_mes = (df4.groupby(by = "mes_y_año")["value"].sum()).reset_index()
df_mes["mes_y_año"] =  pd.to_datetime(df_mes['mes_y_año'], format='%m-%Y')

In [518]:
df_mes.sort_values(by= "mes_y_año", ascending = True, inplace = True)

In [519]:
fig = px.line(df_mes, x = "mes_y_año", y = "value", line_group = None)
fig.show()

In [522]:
año = 2020

df_year3 = df3[df3["datetime"].dt.year == int(año)]
mean_value = df_year3['value'].mean()
fig1 = px.line(df_year3, x = "datetime", y = "value", line_group = None)
fig1.add_shape(go.layout.Shape(
            type = "line",
            x0 = df_year3['datetime'].iloc[0],
            y0 = mean_value,
            x1 = df_year3['datetime'].iloc[-1],
            y1 = mean_value,
            line = dict(color = "black", width = 2, dash = "dot")))
fig1.show()

In [542]:
balance = pd.read_csv("../data/scrap/balance.csv")

In [543]:
balance["datetime"] = pd.to_datetime(balance["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
balance['datetime'] = balance['datetime'].dt.tz_convert('Europe/Paris')
balance["año"] = balance["datetime"].dt.year



In [544]:
balance_no_reno = balance[["value_Turbinación bombeo","value_Nuclear", "value_Ciclo combinado", "value_Carbón", "value_Turbina de gas", "value_Motores diésel", "value_Turbina de vapor", "value_Fuel + Gas", "value_Cogeneración","value_Residuos no renovables"]]*60.25
balance_no_reno.columns = [energia.replace("value_", "") for energia in balance_no_reno.columns]


In [545]:
no_renovables = balance_no_reno.fillna(0).mean().reset_index(name = "value").rename(columns={"index": "Energia"})
no_renovables["Tipo"] = "No Renovable"

In [546]:
balance_reno = balance[["value_Hidráulica","value_Eólica", "value_Solar fotovoltaica", "value_Solar térmica", "value_Otras renovables", "value_Residuos renovables", "value_Hidroeólica"]]*39.75
balance_reno.columns = [energia.replace("value_", "") for energia in balance_reno.columns]


In [547]:
renovables = balance_reno.fillna(0).mean().reset_index(name = "value").rename(columns={"index": "Energia"})
renovables["Tipo"] = "Renovable"

In [548]:
energias = pd.concat([renovables, no_renovables], axis= 0)

In [549]:
energias["value"] = round(energias["value"],2)

In [550]:
energias.sort_values(by= "value", ascending= False, inplace= True)

In [553]:
energias

Energia       value          Tipo
1                 Nuclear  9094016.67  No Renovable
2         Ciclo combinado  6435166.32  No Renovable
1                  Eólica  5829134.56     Renovable
3                  Carbón  4612634.48  No Renovable
8            Cogeneración  4323105.33  No Renovable
0              Hidráulica  3239804.70     Renovable
2      Solar fotovoltaica  1371168.79     Renovable
3           Solar térmica   516012.89     Renovable
5          Motores diésel   497479.20  No Renovable
0      Turbinación bombeo   467384.35  No Renovable
4        Otras renovables   431451.10     Renovable
9  Residuos no renovables   361117.18  No Renovable
6        Turbina de vapor   332517.95  No Renovable
4          Turbina de gas   122471.31  No Renovable
5     Residuos renovables    86828.47     Renovable
6             Hidroeólica     1738.41     Renovable
7              Fuel + Gas      -45.33  No Renovable

In [551]:
fig = px.bar(energias, x='Energia', y='value', color = "Tipo",
    color_discrete_map = {"Renovable":"Green", 'No Renovable':'black'})
fig.show()



In [552]:
fig = px.sunburst(
    energias,
    path = ["Tipo", "Energia"],
    values = "value",
    color = "Tipo",
    color_discrete_map = {"Renovable":"Green", 'No Renovable':'black'})
fig.show();

c:\Users\Lin\anaconda3\lib\site-packages\plotly\express\_core.py:1637: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

c:\Users\Lin\anaconda3\lib\site-packages\plotly\express\_core.py:1637: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [523]:
todas_energias = balance[["datetime","value_Turbinación bombeo","value_Nuclear", "value_Ciclo combinado", "value_Carbón", "value_Turbina de gas", "value_Motores diésel", "value_Turbina de vapor",
                "value_Fuel + Gas", "value_Cogeneración","value_Residuos no renovables", "value_Hidráulica","value_Eólica", "value_Solar fotovoltaica", "value_Solar térmica",
                "value_Otras renovables", "value_Residuos renovables", "value_Hidroeólica"]]
todas_energias.columns = ["datetime"]+[energia.replace("value_","") for energia in todas_energias.drop("datetime", axis = 1).columns]

todas_energias.fillna(0, inplace = True)

C:\Users\Lin\AppData\Local\Temp\ipykernel_3836\2537029453.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [524]:
todas_energias.columns

Index(['datetime', 'Turbinación bombeo', 'Nuclear', 'Ciclo combinado',
       'Carbón', 'Turbina de gas', 'Motores diésel', 'Turbina de vapor',
       'Fuel + Gas', 'Cogeneración', 'Residuos no renovables', 'Hidráulica',
       'Eólica', 'Solar fotovoltaica', 'Solar térmica', 'Otras renovables',
       'Residuos renovables', 'Hidroeólica'],
      dtype='object')

In [525]:
fig = px.line(
    todas_energias,
    x='datetime',
    y=['Turbinación bombeo', 'Nuclear', 'Ciclo combinado',
       'Carbón', 'Turbina de gas', 'Motores diésel', 'Turbina de vapor',
       'Fuel + Gas', 'Cogeneración', 'Residuos no renovables', 'Hidráulica',
       'Eólica', 'Solar fotovoltaica', 'Solar térmica', 'Otras renovables',
       'Residuos renovables', 'Hidroeólica'],
    color_discrete_map = {
    "Turbinación bombeo": "blue", "Nuclear": "green", "Ciclo combinado": "brown",
    "Carbón": "black", "Turbina de gas": "orange", "Motores diésel": "gold", "Turbina de vapor": "cyan",
    "Fuel + Gas": "pink", "Cogeneración": "grey", "Residuos no renovables": "purple", "Hidráulica": "royalblue",
    "Eólica": "lightblue", "Solar fotovoltaica": "yellow", "Solar térmica": "red", "Otras renovables": "violet",
    "Residuos renovables": "yellowgreen", "Hidroeólica": "seashell"})
fig.show()

In [196]:
evolucion_reno = pd.read_csv("../data/evolucion_renovable_no_renovable.csv")
evolucion_reno["datetime"] = pd.to_datetime(evolucion_reno["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
evolucion_reno['datetime'] = evolucion_reno['datetime'].dt.tz_convert('Europe/Paris')

In [529]:
porcentage_reno = round(evolucion_reno["percentage_Renovable"].mean() *100, 2)
porcentage_no_reno = round(evolucion_reno["percentage_No renovable"].mean() *100, 2)

In [533]:
evolucion_reno['mes_y_año'] = evolucion_reno['datetime'].dt.strftime('%m-%Y')
evolucion_reno_mes = (evolucion_reno.groupby(by = "mes_y_año")["percentage_Renovable", "percentage_No renovable"].mean()).reset_index()
evolucion_reno_mes["mes_y_año"] =  pd.to_datetime(evolucion_reno_mes['mes_y_año'], format='%m-%Y')
evolucion_reno_mes.sort_values(by= "mes_y_año", ascending = True, inplace = True)

C:\Users\Lin\AppData\Local\Temp\ipykernel_3836\1440917383.py:2: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [534]:
evolucion_reno_mes

mes_y_año  percentage_Renovable  percentage_No renovable
0   2014-01-01              0.487314                 0.512686
10  2014-02-01              0.556173                 0.443827
20  2014-03-01              0.518892                 0.481108
30  2014-04-01              0.497904                 0.502096
39  2014-05-01              0.423910                 0.576090
..         ...                   ...                      ...
101 2022-11-01              0.462579                 0.537421
110 2022-12-01              0.445510                 0.554490
9   2023-01-01              0.562183                 0.437817
19  2023-02-01              0.448230                 0.551770
29  2023-03-01              0.528342                 0.471658

[111 rows x 3 columns]

In [535]:
mean_value = evolucion_reno_mes["percentage_Renovable"].mean()*100 
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = evolucion_reno_mes['mes_y_año'], y = (evolucion_reno_mes["percentage_Renovable"]*100),
    hoverinfo='x+y',
    mode='lines',
    line=dict(width=0.5, color='green'),
    stackgroup='one',
    name = "Renovable"
))
fig.add_trace(go.Scatter(
    x = evolucion_reno_mes['mes_y_año'], y = (evolucion_reno_mes["percentage_No renovable"]*100),
    hoverinfo='x+y',
    mode='lines',
    line=dict(width=0.5, color='black'),
    stackgroup='one',
    name = "No Renovable"
))
fig.add_shape(go.layout.Shape(
            type = "line",
            x0 = evolucion_reno_mes['mes_y_año'].iloc[0],
            y0 = mean_value,
            x1 = evolucion_reno_mes['mes_y_año'].iloc[-1],
            y1 = mean_value,
            line = dict(color = "black", width = 2, dash = "dot")))
fig.update_layout(yaxis_range=(0, 100))
fig.show()

In [94]:
emisiones = pd.read_csv("../data/emisiones_CO2.csv")

In [97]:
emisiones["datetime"] = pd.to_datetime(emisiones["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
emisiones['datetime'] = emisiones['datetime'].dt.tz_convert('Europe/Paris')
emisiones['mes_y_año'] = emisiones['datetime'].dt.strftime('%m-%Y')
df_mes_emisiones = (emisiones.groupby(by = "mes_y_año")["value_Carbón", "value_Motores diésel", "value_Turbina de gas", "value_Turbina de vapor", "value_Ciclo combinado", "value_Cogeneración", "value_Residuos no renovables"].sum()).reset_index()
df_mes_emisiones["mes_y_año"] =  pd.to_datetime(df_mes_emisiones['mes_y_año'], format='%m-%Y')
df_mes_emisiones.sort_values(by= "mes_y_año", ascending = True, inplace = True)

C:\Users\Lin\AppData\Local\Temp\ipykernel_7164\3246576251.py:4: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [99]:
fig = px.line(df_mes_emisiones, x='mes_y_año', y=["value_Carbón", "value_Motores diésel", "value_Turbina de gas", "value_Turbina de vapor", "value_Ciclo combinado", "value_Cogeneración", "value_Residuos no renovables"])
fig.show()

In [31]:
perdidas = pd.read_csv("../data/perdidas_transporte.csv")

In [537]:
perdidas["datetime"] = pd.to_datetime(perdidas["datetime"], utc = True, format = '%Y-%m-%d %H:%M:%S%z')
perdidas['datetime'] = perdidas['datetime'].dt.tz_convert('Europe/Paris')
perdidas["value"] = (perdidas["value"] * 100)

In [538]:
perdidas2 = perdidas.copy()
perdidas2['mes_y_año'] = perdidas2['datetime'].dt.strftime('%m-%Y')
perdidas2_mes = (perdidas2.groupby(by = "mes_y_año")["value"].mean()).reset_index()
perdidas2_mes["mes_y_año"] =  pd.to_datetime(perdidas2_mes['mes_y_año'], format='%m-%Y')
perdidas2_mes.sort_values(by= "mes_y_año", ascending = True, inplace = True)
fig1 = px.line(perdidas2_mes, x = "mes_y_año", y = "value", line_group = None)
fig1.show()

In [540]:
mean_value = perdidas2_mes["value"].mean()
fig1 = px.line(perdidas2_mes, x = "mes_y_año", y = "value", line_group = None)
fig1.add_shape(go.layout.Shape(
            type = "line",
            x0 = perdidas2_mes['mes_y_año'].iloc[0],
            y0 = mean_value,
            x1 = perdidas2_mes['mes_y_año'].iloc[-1],
            y1 = mean_value,
            line = dict(color = "black", width = 2, dash = "dot")))
fig1.show()